In [ ]:
import glob
import os

os.environ['KERAS_BACKEND'] = 'tensorflow'  # 也可以使用 tensorflow
# os.environ['THEANO_FLAGS']='floatX=float32,device=cuda,exception_verbosity=high'
os.environ['THEANO_FLAGS'] = 'floatX=float32,device=cuda,optimizer=fast_compile'
os.environ["CUDA_VISIBLE_DEVICES"] = "8"

import keras.backend as K

K.set_image_data_format('channels_last')

import time
from keras.models import Sequential, Model
from keras.layers import Conv2D, ZeroPadding2D, BatchNormalization, Input, LSTM, Concatenate, Dense, Dropout
from keras.layers import Conv2DTranspose, Reshape, Activation, Cropping2D, Flatten, UpSampling2D, AveragePooling2D
from keras.layers.advanced_activations import LeakyReLU
from keras.activations import relu
from keras.initializers import RandomNormal
from keras.datasets import mnist
from urllib.request import urlretrieve
from keras.optimizers import RMSprop, SGD, Adam, sgd
import numpy as np
import cv2
import matplotlib.pyplot as plt
from keras.models import model_from_json

# from read_data import *
a = %pwd
print(a)

%run /root/jupyter/inspace/sang-min/myo_proejct/load_data.py import DataLoader
#%load load_data import DataLoader
#from load_data import DataLoader


'''
Model structure

Input : (100) Vector
Output : (64, 64, 1) image

Generator
100 -> 256
256 -> 16 x 16
16 x 16 -> 32 x 32
32 x 32 -> 64 x 64
64 x 64 -> 128 x 128

Discriminator
128 x 128 -> 64 x 64
64 x 64 -> 32 x 32
32 x 32 -> 16 x 16
16 x 16 -> 8 x 8
8 x 8 -> 64
64 -> 32 (16, 10)

'''
loader = DataLoader(data_path='./dataset_2018_05_16/', is_real_image=False)

conv_init = RandomNormal(0, 0.02)
gamma_init = RandomNormal(1., 0.02)

lstm_size = (300, 16)
noise_size = 100
image_size = 128
input_size = 100
image_channel = 1
learning_rate = 2e-4

def sample_generation(num, net_g):
    for _ in range(num):
        gan_image = net_g.predict(noise)
        cv2.imwrite('./model3_output/image/' + 'sample_image'+ str(_) + '.png', gan_image[_] * 127.5)
        
    print("generated image")


def generative_model(noise_size, image_channel):
    # lstm_layer = LSTM(80, input_shape=lstm_size)(lstm_input)
    # _ = Concatenate(axis=-1)([lstm_layer, noise_input])
    print(" _ : ", noise_input)
    _ = Dense(2*2*512, input_shape=(100,), activation='relu', bias_initializer='glorot_normal',
              kernel_initializer='glorot_normal')(noise_input)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Reshape((2, 2, 512), input_shape=(2*2*512,))(_)

    _ = Conv2D(filters=256, kernel_size=(3, 3), strides=1, padding='same', kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = UpSampling2D()(_)
    _ = Conv2D(filters=128, kernel_size=3, padding='same', kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)
    _ = Dropout(0.3)(_)
    
    _ = UpSampling2D()(_)
    _ = Conv2D(filters=64, kernel_size=3, padding='same',  kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)
    #_ = Dropout(0.3)(_)

    _ = UpSampling2D()(_)
    _ = Conv2D(filters=32, kernel_size=3, padding='same', kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)
    _ = Dropout(0.3)(_)
    
    _ = UpSampling2D()(_)
    _ = Conv2D(filters=16, kernel_size=3, padding='same', kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)
    #_ = Dropout(0.3)(_)
    
    _ = UpSampling2D()(_)
    _ = Conv2D(filters=8, kernel_size=3, padding='same', kernel_initializer=conv_init)(_)
    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = LeakyReLU(alpha=0.2)(_)
    _ = Dropout(0.3)(_)
    
    _ = UpSampling2D()(_)
    _ = Conv2D(filters=image_channel, kernel_size=3, padding='same', kernel_initializer=conv_init)(_)
    _ = Activation(activation='tanh')(_)

    return Model(inputs=noise_input, outputs=_)


def discriminative_model(image_size, image_channel):
    _ = inputs = Input(shape=(image_size, image_size, image_channel))

    _ = Conv2D(filters=32, kernel_size=(5, 5), border_mode='same', input_shape=(image_size,image_size, image_channel),
               kernel_initializer=conv_init)(_)
    _ = AveragePooling2D(pool_size=(2, 2), border_mode='valid')(_)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Conv2D(filters=64,kernel_size=(5, 5), border_mode='same', input_shape=(64, 64, 32),
               kernel_initializer=conv_init)(_)
    _ = AveragePooling2D(pool_size=(2, 2), border_mode='valid')(_)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Conv2D(filters=128, kernel_size=(5, 5), border_mode='same', input_shape=(32, 32, 64),
               kernel_initializer=conv_init)(_)
    _ = AveragePooling2D(pool_size=(2, 2), border_mode='valid')(_)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Conv2D(filters=256, kernel_size=(5, 5), border_mode='same', input_shape=(16, 16, 128),
               kernel_initializer=conv_init)(_)
    _ = AveragePooling2D(pool_size=(2, 2), border_mode='valid')(_)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Conv2D(filters=512, kernel_size=(5, 5), border_mode='same', input_shape=(8, 8, 256),
               kernel_initializer=conv_init)(_)
    _ = AveragePooling2D(pool_size=(2, 2), border_mode='valid')(_)
    _ = LeakyReLU(alpha=0.2)(_)

    _ = BatchNormalization(axis=1, gamma_initializer=gamma_init)(_, training=1)
    _ = Conv2D(filters=1, kernel_size=(2, 2), strides=1, padding='same', input_shape=(4, 4, 512),
               kernel_initializer=conv_init)(_)
    # _ = LeakyReLU(alpha=0.2)(_)

    outputs = Flatten()(_)
    outputs = Dense(1, activation='sigmoid')(outputs)

    return Model(inputs=inputs, outputs=outputs)

discriminator_optim = sgd(lr=0.01, momentum=0.9, nesterov=True)
generator_optim = Adam(lr=1e-3)
adam = Adam(lr=0.0002, beta_1=0.5, beta_2=0.999)  # as described in appendix A of DeepMind's AC-GAN paper

# lstm_input = Input(shape=lstm_size)
noise_input = Input(shape=(noise_size,))
real_image = Input(shape=(image_size, image_size, image_channel))

net_g = generative_model(noise_size, image_channel)
fake_image = net_g(noise_input)
net_g.summary()

net_d = discriminative_model(image_size, image_channel)
net_d.summary()

combined_output = net_d(fake_image)
combined_model = Model(inputs=[noise_input], outputs=[combined_output], name='combined')

net_g.compile(loss='binary_crossentropy', optimizer=adam)
net_d.compile(loss='binary_crossentropy', optimizer=adam)
net_d.trainable = False
combined_model.compile(loss='binary_crossentropy', optimizer=adam)

combined_model.summary()

'''
loader = DataLoader(data_path='./MYO_Dataset_label/')

emg = loader.load_emg_data()
image, label = loader.load_image()

print(emg.shape)
print(image.shape, label)

emg = loader.get_emg_datas(10)
images, labels = loader.get_images(10)
print(emg.shape, images.shape, labels.shape)

'''

epoch = 100000
i = 0
time_0 = time.time()
batch_size = 64

d_step = 1
g_step = 1

g_loss_history = []
d_loss_real_history = []
d_loss_fake_history = []

while i <= epoch:
    # x_train = loader.get_emg_datas(batch_size)
    images = loader.get_images(batch_size) / 255.0
    
    for _ in range(d_step):
        noise = np.random.normal(size=[batch_size, noise_size])

        g_z = net_g.predict(noise)
    
        d_loss_real = net_d.train_on_batch(images, np.random.uniform(low=0.7, high=1.2, size=batch_size))
        d_loss_fake = net_d.train_on_batch(g_z, np.random.uniform(low=0.0, high=0.3, size=batch_size))
    
        d_loss_real_history.append(d_loss_real)
        d_loss_fake_history.append(d_loss_fake)
        d_loss = np.sum([d_loss_fake, d_loss_real])    
        
    for _ in range(g_step):
        noise = np.random.normal(size=[batch_size, noise_size])
        combined_loss = combined_model.train_on_batch(noise, np.random.uniform(low=0.7, high=1.2, size=batch_size))
    
        g_loss_history.append(combined_loss)
    
    print("%d [D loss real: %f] [D loss fake: %f] [D loss: %f] [G loss: %f]" % (i, d_loss_real, d_loss_fake, d_loss, combined_loss))
        
    if i % 500 == 0:
        gan_image = net_g.predict(noise)
        print("gan imaga2 : ", gan_image[0].shape)
        cv2.imwrite('./model3_output/image/' + 'fake_image'+ str(i) + '.png', gan_image[0] * 127.5)
        #cv2.imwrite('./output_image3/' + 'real_image'+ str(i) + '.png', images[0] * 127.5)
        
    i +=1;

sample_generation(32, net_g)

net_g.save_weights("./model3_output/save_model/g_model.h5")
net_d.save_weights("./model3_output/save_model/d_model.h5")
combined_model.save_weights("./model3_output/save_model/combined_model.h5")

g_model_json = net_g.to_json()
with open("./model3_output/save_model/g_model.json", "w") as json_file:
    json_file.write(g_model_json)
    
d_model_json = net_d.to_json()
with open("./model3_output/save_model/d_model.json", "w") as json_file:
    json_file.write(d_model_json)

combined_model_json = combined_model.to_json()
with open("./model3_output/save_model/combined_model.json", "w") as json_file:
    json_file.write(combined_model_json)

print("Saved model to disk")

#print("save model ")
plt.figure(1, figsize=(16, 8))
plt.plot(d_loss_real_history)
plt.ylabel('d_loss_real')
plt.xlabel('epoch')
plt.legend(['train'], loc='upper left')

plt.savefig('./model3_output/image/d_loss_real_history.png')

plt.figure(2, figsize=(16, 8))
plt.plot(d_loss_fake_history)
plt.ylabel('d_loss_fake')
plt.xlabel('epoch')
plt.legend(['train'], loc='upper left')

plt.savefig('./model3_output/image/d_loss_fake_history.png')

#plt.show()

plt.figure(3, figsize=(16, 8))
plt.plot(g_loss_history)
plt.ylabel('g_loss')
plt.xlabel('epoch')
plt.legend(['train'], loc='upper left')

plt.savefig('./model3_output/image/g_loss_history.png')

#plt.show()\

plt.show()

print("Finish")

/root/jupyter/inspace/sang-min/myo_proejct
30
./dataset_2018_05_16/1/
15
 _ :  Tensor("input_33:0", shape=(?, 100), dtype=float32)
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_33 (InputLayer)        (None, 100)               0         
_________________________________________________________________
dense_22 (Dense)             (None, 2048)              206848    
_________________________________________________________________
batch_normalization_123 (Bat (None, 2048)              8192      
_________________________________________________________________
reshape_12 (Reshape)         (None, 2, 2, 512)         0         
_________________________________________________________________
conv2d_132 (Conv2D)          (None, 2, 2, 256)         1179904   
_________________________________________________________________
batch_normalization_124 (Bat (None, 2, 2, 256)         8         
___________

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:133: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(filters=32, padding="same", input_shape=(128, 128,..., kernel_size=(5, 5), kernel_initializer=<keras.ini...)`
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:134: UserWarning: Update your `AveragePooling2D` call to the Keras 2 API: `AveragePooling2D(pool_size=(2, 2), padding="valid")`
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:139: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(filters=64, padding="same", input_shape=(64, 64, 3..., kernel_size=(5, 5), kernel_initializer=<keras.ini...)`
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:140: UserWarning: Update your `AveragePooling2D` call to the Keras 2 API: `AveragePooling2D(pool_size=(2, 2), padding="valid")`
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:145: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(fil

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_35 (InputLayer)        (None, 128, 128, 1)       0         
_________________________________________________________________
conv2d_139 (Conv2D)          (None, 128, 128, 32)      832       
_________________________________________________________________
average_pooling2d_51 (Averag (None, 64, 64, 32)        0         
_________________________________________________________________
leaky_re_lu_117 (LeakyReLU)  (None, 64, 64, 32)        0         
_________________________________________________________________
batch_normalization_130 (Bat (None, 64, 64, 32)        256       
_________________________________________________________________
conv2d_140 (Conv2D)          (None, 64, 64, 64)        51264     
_________________________________________________________________
average_pooling2d_52 (Averag (None, 32, 32, 64)        0         
__________

/usr/local/lib/python3.5/dist-packages/keras/engine/training.py:973: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


0 [D loss real: 1.273418] [D loss fake: 1.867440] [D loss: 3.140859] [G loss: 4.061225]
gan imaga2 :  (128, 128, 1)
1 [D loss real: 0.518013] [D loss fake: 1.162431] [D loss: 1.680443] [G loss: 4.732301]
2 [D loss real: 0.307912] [D loss fake: 0.851251] [D loss: 1.159163] [G loss: 1.951411]
3 [D loss real: 2.169291] [D loss fake: 0.480506] [D loss: 2.649796] [G loss: 1.887522]
4 [D loss real: 0.702825] [D loss fake: 0.432471] [D loss: 1.135295] [G loss: 3.702187]
5 [D loss real: 0.688568] [D loss fake: 1.481693] [D loss: 2.170260] [G loss: 3.769637]
6 [D loss real: 0.320487] [D loss fake: 2.601757] [D loss: 2.922243] [G loss: 2.932441]
7 [D loss real: 0.377124] [D loss fake: 1.054374] [D loss: 1.431498] [G loss: 3.052701]
8 [D loss real: 0.342312] [D loss fake: 2.592845] [D loss: 2.935157] [G loss: 6.368979]
9 [D loss real: 0.234905] [D loss fake: 0.910273] [D loss: 1.145179] [G loss: 6.183681]
10 [D loss real: 0.315823] [D loss fake: 0.729113] [D loss: 1.044937] [G loss: 3.024578]
11 

...

70254 [D loss real: 0.214677] [D loss fake: 0.434308] [D loss: 0.648984] [G loss: 0.216472]
70255 [D loss real: 0.139699] [D loss fake: 0.408324] [D loss: 0.548024] [G loss: 0.248626]
70256 [D loss real: 0.215374] [D loss fake: 0.452651] [D loss: 0.668025] [G loss: 0.169257]
70257 [D loss real: 0.173664] [D loss fake: 0.420315] [D loss: 0.593979] [G loss: 0.251409]
70258 [D loss real: 0.137693] [D loss fake: 0.419461] [D loss: 0.557153] [G loss: 0.174677]
70259 [D loss real: 0.102664] [D loss fake: 0.418304] [D loss: 0.520969] [G loss: 0.140417]
./dataset_2018_05_16/6/
70260 [D loss real: 0.101400] [D loss fake: 0.399515] [D loss: 0.500915] [G loss: 0.271776]
70261 [D loss real: 0.143394] [D loss fake: 0.437071] [D loss: 0.580465] [G loss: 0.171873]
70262 [D loss real: 0.090436] [D loss fake: 0.450977] [D loss: 0.541413] [G loss: 0.196924]
70263 [D loss real: 0.252737] [D loss fake: 0.464055] [D loss: 0.716791] [G loss: 0.173972]
70264 [D loss real: 0.201079] [D loss fake: 0.412164] [D

70342 [D loss real: 0.227337] [D loss fake: 0.458171] [D loss: 0.685508] [G loss: 0.247005]
70343 [D loss real: 0.162851] [D loss fake: 0.438190] [D loss: 0.601040] [G loss: 0.190700]
./dataset_2018_05_16/12/
70344 [D loss real: 0.204962] [D loss fake: 0.427974] [D loss: 0.632937] [G loss: 0.215797]
70345 [D loss real: 0.120157] [D loss fake: 0.416971] [D loss: 0.537128] [G loss: 0.192375]
70346 [D loss real: 0.195870] [D loss fake: 0.430030] [D loss: 0.625900] [G loss: 0.251189]
70347 [D loss real: 0.263629] [D loss fake: 0.429072] [D loss: 0.692701] [G loss: 0.131547]
70348 [D loss real: 0.231950] [D loss fake: 0.412834] [D loss: 0.644783] [G loss: 0.244747]
70349 [D loss real: 0.202535] [D loss fake: 0.412051] [D loss: 0.614586] [G loss: 0.201727]
70350 [D loss real: 0.262051] [D loss fake: 0.424438] [D loss: 0.686489] [G loss: 0.145137]
70351 [D loss real: 0.267744] [D loss fake: 0.419169] [D loss: 0.686913] [G loss: 0.226851]
70352 [D loss real: 0.231920] [D loss fake: 0.425401] [

70431 [D loss real: 0.158533] [D loss fake: 0.432168] [D loss: 0.590701] [G loss: 0.254037]
70432 [D loss real: 0.267074] [D loss fake: 0.432614] [D loss: 0.699688] [G loss: 0.241220]
70433 [D loss real: 0.162577] [D loss fake: 0.412235] [D loss: 0.574812] [G loss: 0.180253]
70434 [D loss real: 0.174338] [D loss fake: 0.425201] [D loss: 0.599539] [G loss: 0.169025]
70435 [D loss real: 0.199186] [D loss fake: 0.415929] [D loss: 0.615116] [G loss: 0.186102]
70436 [D loss real: 0.207665] [D loss fake: 0.413229] [D loss: 0.620894] [G loss: 0.265666]
70437 [D loss real: 0.227226] [D loss fake: 0.433974] [D loss: 0.661200] [G loss: 0.223051]
70438 [D loss real: 0.146496] [D loss fake: 0.414891] [D loss: 0.561387] [G loss: 0.262599]
70439 [D loss real: 0.203381] [D loss fake: 0.406045] [D loss: 0.609426] [G loss: 0.252932]
70440 [D loss real: 0.208145] [D loss fake: 0.418867] [D loss: 0.627013] [G loss: 0.208439]
70441 [D loss real: 0.239796] [D loss fake: 0.426930] [D loss: 0.666726] [G loss

70519 [D loss real: 0.196821] [D loss fake: 0.415296] [D loss: 0.612117] [G loss: 0.221472]
70520 [D loss real: 0.216499] [D loss fake: 0.429059] [D loss: 0.645558] [G loss: 0.157043]
70521 [D loss real: 0.168922] [D loss fake: 0.406806] [D loss: 0.575728] [G loss: 0.164929]
70522 [D loss real: 0.201923] [D loss fake: 0.409135] [D loss: 0.611058] [G loss: 0.277499]
70523 [D loss real: 0.151854] [D loss fake: 0.387016] [D loss: 0.538870] [G loss: 0.148852]
70524 [D loss real: 0.307036] [D loss fake: 0.398509] [D loss: 0.705545] [G loss: 0.295297]
70525 [D loss real: 0.278044] [D loss fake: 0.418776] [D loss: 0.696821] [G loss: 0.109664]
70526 [D loss real: 0.227861] [D loss fake: 0.378321] [D loss: 0.606182] [G loss: 0.239089]
./dataset_2018_05_16/10/
70527 [D loss real: 0.173388] [D loss fake: 0.427349] [D loss: 0.600738] [G loss: 0.120864]
70528 [D loss real: 0.137959] [D loss fake: 0.431850] [D loss: 0.569809] [G loss: 0.176312]
70529 [D loss real: 0.100944] [D loss fake: 0.446668] [

70608 [D loss real: 0.177476] [D loss fake: 0.406844] [D loss: 0.584319] [G loss: 0.174056]
70609 [D loss real: 0.166072] [D loss fake: 0.390859] [D loss: 0.556931] [G loss: 0.204308]
70610 [D loss real: 0.156769] [D loss fake: 0.413127] [D loss: 0.569896] [G loss: 0.185309]
./dataset_2018_05_16/1/
70611 [D loss real: 0.158028] [D loss fake: 0.458194] [D loss: 0.616222] [G loss: 0.169137]
70612 [D loss real: 0.213856] [D loss fake: 0.421111] [D loss: 0.634967] [G loss: 0.249055]
70613 [D loss real: 0.193887] [D loss fake: 0.447633] [D loss: 0.641520] [G loss: 0.189848]
70614 [D loss real: 0.203317] [D loss fake: 0.421017] [D loss: 0.624334] [G loss: 0.246581]
70615 [D loss real: 0.218798] [D loss fake: 0.408417] [D loss: 0.627215] [G loss: 0.202487]
